In [1]:
#//LIBRARIES
import math
import numpy as np
import pandas as pd

import sys
import os 
sys.path.append(os.path.expanduser('~'))

from analysts_tools.growth import *

#Procurement tools
from procurement_lib import send_slack_notification,GoogleSheet,redash
from analystcommunity.read_connection_data_warehouse import run_read_dwd_query

from datetime import datetime, timedelta

In [2]:
df_sheet=GoogleSheet("1mkqot1agSekg1czi6PU8Qv5vS8niK6MQTnSHaBRIqPU")
df_join = df_sheet.get_as_dataframe('70')

In [3]:
df_bench_info = pd.read_excel("painel_geral (3).xlsx")
df_bench_info1 = df_bench_info.merge(df_join, left_on=['Identificador Produto'],right_on='ean',how='inner')
df_bench_info1['quotation_date'] = pd.to_datetime(df_bench_info1['quotation_date'], format='%d/%m/%Y').dt.strftime('%Y-%m-%d')

In [ ]:
len(df_bench_info1.competitor_name.unique())

320

In [5]:
# Info bench fru

query = """
select
    cpp.collected_product_prices_id,
    quotation_date.full_date AS quotation_date,
    competitor.competitor_name,
    source_type.description as source_type,
    cat.parent_description as category,
    su.source_id,
    su.description,
    cpp.product_selected_price::float as price
from dpr_product_pricing.fact_collected_product_prices cpp
    inner join dpr_shared.dim_date quotation_date
        on cpp.dim_quotation_date = quotation_date.date_id
    inner join dpr_shared.dim_time quotation_time
        on cpp.dim_quotation_time = quotation_time.time_id
    inner join dpr_shared.dim_site site
        on cpp.dim_site = site.site_id
    inner join dpr_shared.dim_category cat
        on cpp.dim_category = cat.category_id
    inner join dpr_product_pricing.dim_product_outlier_type outlier_type
        on cpp.dim_outlier_type = outlier_type.outlier_type_id
    inner join dpr_product_pricing.dim_product_source_type source_type
        on cpp.dim_source_type = source_type.source_type_id
    inner join dpr_product_pricing.dim_product_competitor competitor
        on cpp.dim_competitor = competitor.competitor_id
   inner join dpr_product_pricing.dim_product_competitor_type competitor_type 
        on cpp.dim_product_competitor_type = competitor_type.competitor_type_id
    inner join dpr_shared.dim_stock_unit su
        on cpp.dim_stock_unit = su.stock_unit_id
where quotation_date.full_date > '2024-11-20'-30
    and site.identifier_value = 'SPO'
    AND source_type.description IN ('Zukkin','Scrapers','Infoprice')
    AND competitor_type.description='Main_Competitor'
    AND (
        competitor.competitor_name NOT ILIKE '%cayena%'
        AND competitor.competitor_name <> 'Atacadao_V2'
    )
    and su.source_parent_id = 0
    and su.source_id in {skus}
""".format(skus=tuple(df_join.source_id.unique()))
df_bench_fru = run_read_dwd_query(query)

In [6]:
# Function to calculate the required statistics
def calculate_statistics(df):
    return df.groupby(['quotation_date','source_id'])['price'].agg(
        num_data_points='count',
        num_competitors=lambda x: df.loc[x.index, 'competitor_name'].nunique(),
        min_price='min',
        avg_price='mean',
        median_price='median',
        max_price='max',
        #delta_min_max=lambda x: x.max() - x.min()
    ).reset_index()

In [7]:
def get_info(df_zkkkkk):
    # Ensure dataframe is sorted by 'quotation_date'
    df_zkkkkk = df_zkkkkk.sort_values(by='quotation_date')
    df_zkkkkk['quotation_date'] = pd.to_datetime(df_zkkkkk['quotation_date'], errors='coerce')


    # Generate the required rows for missing dates
    new_rows = []

    for (competitor, source_id), group in df_zkkkkk.groupby(['competitor_name', 'source_id']):
        group = group.sort_values(by='quotation_date')
        group['quotation_date'] = pd.to_datetime(group['quotation_date'], errors='coerce')
        last_known_price = None
        last_known_date = None
        lifetime = 8
        
        for current_index in range(len(group)):
            current_date = group.iloc[current_index]['quotation_date']
            price = group.iloc[current_index]['price']
            
            # If this is not the first iteration, fill in missing dates
            if last_known_date is not None:
                days_diff = (current_date - last_known_date).days
                if days_diff > 1:
                    for j in range(1, min(days_diff, lifetime + 1)):
                        new_date = last_known_date + timedelta(days=j)
                        new_row = {
                            'quotation_date': new_date,
                            'competitor_name': competitor,
                            'source_id': source_id,
                            'price': last_known_price,
                            'lifetime': lifetime - j
                        }
                        new_rows.append(new_row)
                        
                        # Stop if we reach a new datapoint date
                        if new_date + timedelta(days=1) == current_date:
                            break
            
            # Update the last known values and reset lifetime
            last_known_price = price
            last_known_date = current_date
            lifetime = 8  # Reset lifetime

        # After processing all known dates for the group, continue generating rows until lifetime reaches 0
        while lifetime > 0:
            last_known_date += timedelta(days=1)
            new_row = {
                'quotation_date': last_known_date,
                'competitor_name': competitor,
                'source_id': source_id,
                'price': last_known_price,
                'lifetime': lifetime - 1
            }
            new_rows.append(new_row)
            lifetime -= 1

    # Append new rows to the dataframe
    df_zkkkkk = df_zkkkkk.append(new_rows, ignore_index=True)

    df_bench = df_zkkkkk.copy()

    # Calculate statistics for all competitors
    stats_all = calculate_statistics(df_bench)
    stats_all.columns = ['quotation_date','source_id', 'POINTS Med ALL', 'num_competitors_all', 'min_price_all', 'avg_price_all', 'Med ALL', 'max_price_all']

    # Filter for competitors that include "assai" in their name and calculate statistics
    df_assai = df_bench[df_bench['competitor_name'].str.contains(r'assai|assaí', case=False, na=False, regex=True)]
    stats_assai = calculate_statistics(df_assai)
    stats_assai.columns = ['quotation_date','source_id', 'POINTS Med Assai', 'num_competitors_assai', 'min_price_assai', 'avg_price_assai', 'Med Assai', 'max_price_assai']

    # Filter for competitors that include "atacadao" or "atacadão" in their name and calculate statistics
    df_atacadao = df_bench[df_bench['competitor_name'].str.match(r'(?i)^atacad[aã]o') & ~df_bench['competitor_name'].str.contains(r'(?i)^Atacadao_V2$')]
    stats_atacadao = calculate_statistics(df_atacadao)
    stats_atacadao.columns = ['quotation_date','source_id', 'POINTS Med Atacadao', 'num_competitors_atacadao', 'min_price_atacadao', 'avg_price_atacadao', 'Med Atacadao', 'max_price_atacadao']

    # # Filter for competitors that include "atacadao_v2" the scrapper
    # df_scrapper_atacadao = df_bench[df_bench['competitor_name'].str.contains(r'(?i)^Atacadao_V2$')]
    # stats_scrapper_atacadao = calculate_statistics(df_scrapper_atacadao)
    # stats_scrapper_atacadao.columns = ['quotation_date','source_id', 'POINTS Scrp. Atacadao', 'num_competitors_atacadao_scrapper', 'Scrp. Atacadao', 'avg_price_atacadao_scrapper', 'Med atacadao_scrapper', 'max_price_atacadao_scrapper']

    # Merge the results
    bench_df = stats_all.merge(stats_assai, on=['quotation_date','source_id'], how='left').merge(stats_atacadao, on=['quotation_date','source_id'], how='left')#.merge(stats_scrapper_atacadao, on=['quotation_date','source_id'], how='left')

    return bench_df,df_zkkkkk[['quotation_date','competitor_name','source_id','price','lifetime']],df_assai

In [8]:
bench_fru,check_fru,df_assai2 = get_info(df_bench_fru)

In [9]:
bench_info,check_info,df_assai3 = get_info(df_bench_info1)

In [10]:
bench_info.describe()

source_id  POINTS Med ALL  num_competitors_all  min_price_all  \
count    5496.000000     5496.000000          5496.000000    5496.000000   
mean   556224.360262       21.600255            21.595160      16.512445   
std    161742.067395       32.844844            32.830544      20.076937   
min    122237.000000        1.000000             1.000000       0.560000   
25%    514249.000000        3.000000             3.000000       4.590000   
50%    648599.000000       11.000000            11.000000       8.980000   
75%    653093.000000       21.000000            21.000000      21.900000   
max    656226.000000      183.000000           183.000000     159.900000   

       avg_price_all      Med ALL  max_price_all  POINTS Med Assai  \
count    5496.000000  5496.000000    5496.000000       2235.000000   
mean       17.994469    17.901374      19.774745         17.405817   
std        21.413210    20.939994      24.445681         21.905949   
min         0.822031     0.800000       0.950000          1.000000   
25%         5.379028     5.445000       5.990000          3.000000   
50%         9.980000     9.900000      11.800000          8.000000   
75%        24.050000    23.990000      25.500000         25.000000   
max       174.297500   164.900000     219.990000        116.000000   

       num_competitors_assai  min_price_assai  avg_price_assai    Med Assai  \
count            2235.000000      2235.000000      2235.000000  2235.000000   
mean               17.399553        15.341673        16.220981    16.234940   
std                21.878481        15.828893        16.486684    16.481525   
min                 1.000000         0.700000         0.770000     0.760000   
25%                 3.000000         4.790000         5.494063     5.690000   
50%                 8.000000         8.850000         9.336154     9.190000   
75%                25.000000        23.500000        25.500000    25.500000   
max               116.000000        79.000000        79.166667    79.000000   

       max_price_assai  POINTS Med Atacadao  num_competitors_atacadao  \
count      2235.000000          1976.000000               1976.000000   
mean         17.063664            10.748482                 10.748482   
std          17.170928            10.752262                 10.752262   
min           0.790000             1.000000                  1.000000   
25%           6.250000             2.000000                  2.000000   
50%          10.500000             7.000000                  7.000000   
75%          27.000000            16.000000                 16.000000   
max          79.500000            54.000000                 54.000000   

       min_price_atacadao  avg_price_atacadao  Med Atacadao  \
count         1976.000000         1976.000000   1976.000000   
mean            14.463335           15.073376     15.145749   
std             14.927227           15.506870     15.618092   
min              0.850000            0.863333      0.850000   
25%              4.690000            4.800000      4.850000   
50%              8.690000            8.950000      8.980000   
75%             19.900000           19.900000     19.900000   
max             79.900000           79.900000     79.900000   

       max_price_atacadao  
count         1976.000000  
mean            15.496508  
std             16.020574  
min              0.890000  
25%              4.950000  
50%              8.990000  
75%             20.410000  
max             79.900000

In [11]:
bench_fru.describe()

source_id  POINTS Med ALL  num_competitors_all  min_price_all  \
count    5026.000000     5026.000000          5026.000000    5026.000000   
mean   526679.825507        4.142459             4.141663      22.266799   
std    176850.258802        4.085601             4.083534      26.229793   
min    124907.000000        1.000000             1.000000       1.190000   
25%    382155.000000        1.000000             1.000000       5.800000   
50%    633613.000000        2.000000             2.000000      16.900000   
75%    652827.000000        5.000000             5.000000      26.900000   
max    656533.000000       17.000000            17.000000     215.900000   

       avg_price_all      Med ALL  max_price_all  POINTS Med Assai  \
count    5026.000000  5026.000000    5026.000000       2362.000000   
mean       23.967179    23.712264      26.024192          2.353091   
std        27.108830    26.955345      29.934822          1.272576   
min         1.305000     1.190000       1.450000          1.000000   
25%         6.065000     5.990000       6.490000          1.000000   
50%        17.700000    17.900000      18.250000          2.000000   
75%        28.990000    28.880000      31.900000          3.000000   
max       215.900000   215.900000     215.900000          5.000000   

       num_competitors_assai  min_price_assai  avg_price_assai    Med Assai  \
count            2362.000000      2362.000000      2362.000000  2362.000000   
mean                2.353091        20.149763        21.040952    21.087656   
std                 1.272576        13.626400        14.171232    14.252289   
min                 1.000000         1.190000         1.190000     1.190000   
25%                 1.000000         9.500000         9.879375     9.900000   
50%                 2.000000        18.900000        20.130000    19.900000   
75%                 3.000000        26.900000        27.900000    27.900000   
max                 5.000000        71.269000        71.269000    71.269000   

       max_price_assai  POINTS Med Atacadao  num_competitors_atacadao  \
count      2362.000000          3446.000000               3446.000000   
mean         21.851381             2.107661                  2.106500   
std          14.900961             1.318954                  1.316184   
min           1.190000             1.000000                  1.000000   
25%          10.400000             1.000000                  1.000000   
50%          20.600000             2.000000                  2.000000   
75%          28.625000             3.000000                  3.000000   
max          71.269000             6.000000                  5.000000   

       min_price_atacadao  avg_price_atacadao  Med Atacadao  \
count         3446.000000         3446.000000   3446.000000   
mean            22.463019           23.047272     23.064819   
std             22.709776           22.777158     22.799777   
min              1.190000            1.190000      1.190000   
25%              6.590000            6.790000      6.690000   
50%             17.900000           18.499000     17.980000   
75%             28.942500           29.500000     29.500000   
max            159.900000          159.900000    159.900000   

       max_price_atacadao  
count          3446.00000  
mean             23.56581  
std              22.89304  
min               1.19000  
25%               6.99000  
50%              19.90000  
75%              29.99000  
max             159.90000

In [ ]:
import plotly.graph_objects as go
import ipywidgets as widgets
from ipywidgets import interact

# Assuming df1 is bench_fru and df2 is bench_info, we add a 'company' column
bench_fru['company'] = 'Frubana'
bench_info['company'] = 'Infoprice'

# Concatenate both dataframes
df = pd.concat([bench_fru, bench_info])

# Function to plot the data for a selected source_id and metric
def plot_price_trends(source_id, metric):
    # Filter data based on the selected source_id
    filtered_df = df[df['source_id'] == source_id]

    # Create the figure
    fig = go.Figure()

    # Plot lines for both companies
    for company_name, color in [('Frubana', 'blue'), ('Infoprice', 'orange')]:
        company_df = filtered_df[filtered_df['company'] == company_name]
        fig.add_trace(go.Scatter(
            x=company_df['quotation_date'],
            y=company_df[metric],
            mode='lines',
            name=company_name,
            line=dict(color=color)
        ))

    # Update the layout
    fig.update_layout(
        title=f'Price Trends for {df_join.loc[df_join.source_id==source_id].description.values[0]} {source_id} ({metric})',
        xaxis_title='Quotation Date',
        yaxis_title=f'Median Price ({metric})',
        showlegend=True,
        template='plotly_white'
    )

    # Show the figure
    fig.show()

# Get the unique source_ids from the data
source_ids = df['source_id'].unique()

# Create dropdown widgets for `source_id` and `metric`
source_id_dropdown = widgets.Dropdown(
    options=source_ids,
    description='Source ID:',
    value=source_ids[0]  # Default to the first source_id
)

metric_dropdown = widgets.Dropdown(
    options=['Med ALL', 'Med Assai', 'Med Atacadao'],
    description='Metric:',
    value='Med ALL'  # Default to 'Med ALL'
)

# Use the interact function to make the plot interactive
interact(plot_price_trends, source_id=source_id_dropdown, metric=metric_dropdown)

In [13]:
df.loc[df.source_id != 588033,['source_id','company','POINTS Med ALL','POINTS Med Assai','POINTS Med Atacadao']].groupby(['source_id','company']).describe().head(60)

POINTS Med ALL                                       \
                             count        mean        std   min     25%   
source_id company                                                         
122237.0  Infoprice            9.0    1.000000   0.000000   1.0    1.00   
122612.0  Infoprice           38.0    3.842105   0.369537   3.0    4.00   
124907.0  Frubana             38.0   10.315789   2.279228   3.0    9.00   
          Infoprice           38.0   28.236842   7.186452  15.0   24.00   
154464.0  Frubana             38.0   14.210526   2.120147   3.0   14.00   
          Infoprice           38.0  140.947368  46.575105  14.0  114.00   
154481.0  Frubana             38.0    5.868421   1.398282   1.0    5.00   
          Infoprice           38.0   29.684211   4.120517  25.0   27.00   
160692.0  Frubana             38.0    1.631579   0.488852   1.0    1.00   
          Infoprice           36.0    8.305556   3.395959   1.0    6.00   
161273.0  Frubana             18.0    1.000000   0.000000   1.0    1.00   
          Infoprice            9.0    1.000000   0.000000   1.0    1.00   
161297.0  Frubana             37.0    3.243243   0.434959   3.0    3.00   
          Infoprice           38.0   15.473684   3.029020  12.0   13.00   
163392.0  Frubana             37.0    2.594595   1.066132   1.0    2.00   
165406.0  Infoprice            9.0    1.000000   0.000000   1.0    1.00   
166040.0  Frubana             38.0    3.394737   0.594546   2.0    3.00   
          Infoprice           32.0    8.218750   4.870811   1.0    3.75   
168237.0  Frubana             37.0    2.351351   0.587661   2.0    2.00   
          Infoprice           38.0   16.842105   3.009232  11.0   14.25   
173909.0  Frubana             37.0    2.135135   0.630791   1.0    2.00   
          Infoprice           38.0    7.921053   0.911832   7.0    7.00   
173913.0  Frubana             16.0    1.000000   0.000000   1.0    1.00   
          Infoprice            9.0    1.000000   0.000000   1.0    1.00   
173915.0  Frubana             16.0    1.000000   0.000000   1.0    1.00   
173917.0  Frubana             16.0    1.000000   0.000000   1.0    1.00   
173919.0  Frubana             16.0    1.000000   0.000000   1.0    1.00   
          Infoprice            9.0    1.000000   0.000000   1.0    1.00   
173921.0  Frubana             16.0    1.000000   0.000000   1.0    1.00   
173923.0  Frubana              9.0    1.000000   0.000000   1.0    1.00   
173925.0  Frubana             16.0    1.000000   0.000000   1.0    1.00   
          Infoprice            9.0    1.000000   0.000000   1.0    1.00   
202839.0  Frubana             38.0    7.394737   1.952676   2.0    7.00   
          Infoprice           38.0   15.131579   3.473226  11.0   12.00   
225217.0  Frubana             16.0    1.000000   0.000000   1.0    1.00   
236589.0  Frubana              9.0    1.000000   0.000000   1.0    1.00   
240310.0  Frubana             37.0    1.000000   0.000000   1.0    1.00   
          Infoprice           38.0   14.236842   0.430851  14.0   14.00   
240407.0  Infoprice           10.0    1.800000   0.421637   1.0    2.00   
240437.0  Frubana             16.0    1.125000   0.341565   1.0    1.00   
          Infoprice           38.0   12.236842   0.913390  11.0   11.00   
240490.0  Frubana             37.0    3.405405   1.117026   2.0    2.00   
240496.0  Frubana             37.0    1.000000   0.000000   1.0    1.00   
          Infoprice           38.0   14.368421   0.488852  14.0   14.00   
240511.0  Frubana             32.0    1.906250   1.027348   1.0    1.00   
241589.0  Frubana             16.0    1.125000   0.341565   1.0    1.00   
          Infoprice           37.0   22.432432   9.731223   1.0   17.00   
243407.0  Frubana             38.0   15.368421   2.222989   3.0   15.00   
          Infoprice           38.0  109.236842  35.769105  30.0   80.00   
243663.0  Frubana             38.0   13.842105   2.646020   3.0   13.00   
247589.0  Frubana              9.0    1.00000

In [14]:
import plotly.graph_objects as go
import pandas as pd

# Supongamos que los DataFrames `bench_fru` y `bench_info` ya están definidos
# y contienen las columnas 'source_id', 'quotation_date', y los valores de métricas

# Añadimos la columna 'company'
bench_fru['company'] = 'Frubana'
bench_info['company'] = 'Infoprice'

# Concatenamos ambos DataFrames
df = pd.concat([bench_fru, bench_info])

# Obtenemos los source_ids únicos
source_ids = df['source_id'].unique()

# Recorremos todos los source_ids y graficamos para cada uno
for source_id in source_ids:
    # Filtrar los datos por el source_id actual
    filtered_df = df[df['source_id'] == source_id]

    # Crear la figura
    fig = go.Figure()

    # Añadir las líneas para cada compañía
    for company_name, color in [('Frubana', 'blue'), ('Infoprice', 'orange')]:
        company_df = filtered_df[filtered_df['company'] == company_name]
        fig.add_trace(go.Scatter(
            x=company_df['quotation_date'],
            y=company_df['Med ALL'],  # Usar siempre 'Med ALL'
            mode='lines',
            name=f'{company_name} - {source_id}',
            line=dict(color=color)
        ))

    # Actualizar el diseño
    fig.update_layout(
        title=f'Price Trends for {df_join.loc[df_join.source_id==source_id].description.values[0]} {source_id} (Med ALL)',
        xaxis_title='Quotation Date',
        yaxis_title='Median Price (Med ALL)',
        showlegend=True,
        template='plotly_white'
    )

    # Mostrar la figura
    fig.show()


In [15]:
# Step 1: Filter source_id values only present for "Infoprice"
source_ids_only_Infoprice = (
    df[df['company'] == 'Infoprice']['source_id']
    .unique()
)
source_ids_only_Infoprice = [
    src_id for src_id in source_ids_only_Infoprice
    if src_id not in df[df['company'] == 'Frubana']['source_id'].unique()
]

# Step 1: Filter source_id values only present for "Infoprice"
source_ids_only_Frubana = (
    df[df['company'] == 'Frubana']['source_id']
    .unique()
)
source_ids_only_Frubana = [
    src_id for src_id in source_ids_only_Frubana
    if src_id not in df[df['company'] == 'Infoprice']['source_id'].unique()
]

# Step 2: Calculate the variance of `Med ALL` for `source_id` with both companies
source_ids_with_both = df['source_id'].unique()
variances = []

for src_id in source_ids_with_both:
    subset = df[df['source_id'] == src_id]
    
    # Check if the source_id has data for both companies
    if set(subset['company'].unique()) == {'Frubana', 'Infoprice'}:
        # Pivot to align `Med ALL` values by `quotation_date`
        pivot = subset.pivot_table(
            index='quotation_date', 
            columns='company', 
            values='Med ALL'
        )
        
        # Drop rows with missing values
        pivot.dropna(inplace=True)
        
        # Calculate variance for overlapping dates
        if not pivot.empty:
            variance = ((pivot['Frubana'] - pivot['Infoprice']) ** 2).mean()
            variances.append({'source_id': src_id, 'avg_variance': variance})

# Step 3: Sort `source_id` by average variance
sorted_variances = sorted(variances, key=lambda x: x['avg_variance'])

# Extract sorted source_id list
sorted_source_ids = [item['source_id'] for item in sorted_variances]

# Results
print("Source IDs only for 'Infoprice':", source_ids_only_Infoprice)
print("Sorted Source IDs based on average variance:", sorted_source_ids)


Source IDs only for 'Infoprice': [122237.0, 122612.0, 165406.0, 240407.0, 320739.0, 361022.0, 361025.0, 509492.0, 509498.0, 514243.0, 644479.0, 645792.0, 649861.0, 649865.0, 652293.0, 652299.0, 652811.0, 652861.0, 652979.0, 654027.0, 654107.0, 654117.0, 654121.0, 654594.0, 655597.0, 655599.0, 655603.0, 655605.0, 655609.0, 655611.0, 656035.0, 656210.0, 656220.0, 628488.0, 628496.0, 652301.0, 652883.0, 654379.0, 655601.0, 361001.0, 633633.0, 639503.0, 655155.0, 361004.0, 652851.0, 656063.0, 649783.0, 652879.0, 655687.0, 656226.0, 382171.0, 582043.0, 621475.0, 633841.0, 652327.0, 633849.0, 654600.0]
Sorted Source IDs based on average variance: [160692.0, 653493.0, 652539.0, 653491.0, 154464.0, 652835.0, 653093.0, 652827.0, 648637.0, 652313.0, 652297.0, 654105.0, 654469.0, 648631.0, 653639.0, 648603.0, 653489.0, 648599.0, 652981.0, 243407.0, 652875.0, 648623.0, 648605.0, 652983.0, 627436.0, 649823.0, 241589.0, 653091.0, 546125.0, 652993.0, 572864.0, 649777.0, 633851.0, 653095.0, 397299.0, 

In [16]:
# Lista completa de source_id únicos en el DataFrame
all_source_ids = set(df['source_id'].unique())

# Unir todas las listas conocidas
known_source_ids = set(source_ids_only_infoprice) | set(sorted_source_ids) | set(source_ids_only_Frubana)

# Identificar los source_id que no están en las listas conocidas
missing_source_ids = all_source_ids - known_source_ids

# Mostrar los resultados
print("Source IDs no clasificados:", len(missing_source_ids))

NameError: name 'source_ids_only_infoprice' is not defined

In [ ]:
print(len(source_ids_only_Infoprice),len(sorted_source_ids),len(source_ids_only_Frubana))

57 121 58


In [ ]:
import plotly.graph_objects as go
import pandas as pd

sorted_check = [item['source_id'] for item in sorted_variances[-50:]]

# Supongamos que los DataFrames `bench_fru` y `bench_info` ya están definidos
# y contienen las columnas 'source_id', 'quotation_date', y los valores de métricas

# Añadimos la columna 'company'
bench_fru['company'] = 'Frubana'
bench_info['company'] = 'Infoprice'

# Concatenamos ambos DataFrames
df = pd.concat([bench_fru, bench_info])

# Obtenemos los source_ids únicos
source_ids = df.loc[df.source_id.isin(sorted_check)]['source_id'].unique()

# Recorremos todos los source_ids y graficamos para cada uno
for source_id in source_ids:
    # Filtrar los datos por el source_id actual
    filtered_df = df[df['source_id'] == source_id]

    # Crear la figura
    fig = go.Figure()

    # Añadir las líneas para cada compañía
    for company_name, color in [('Frubana', 'blue'), ('Infoprice', 'orange')]:
        company_df = filtered_df[filtered_df['company'] == company_name]
        fig.add_trace(go.Scatter(
            x=company_df['quotation_date'],
            y=company_df['Med ALL'],  # Usar siempre 'Med ALL'
            mode='lines',
            name=f'{company_name} - {source_id}',
            line=dict(color=color)
        ))

    # Actualizar el diseño
    fig.update_layout(
        title=f'Price Trends for {df_join.loc[df_join.source_id==source_id].description.values[0]} {source_id} (Med ALL)',
        xaxis_title='Quotation Date',
        yaxis_title='Median Price (Med ALL)',
        showlegend=True,
        template='plotly_white'
    )

    # Mostrar la figura
    fig.show()
